In [1]:
import pandas as pd
import numpy as np

from sklearn.preprocessing import MinMaxScaler
from mat4py import loadmat

try:
    pd.options.plotting.backend = "plotly"
except ValueError:
    print("plotly não encontrado. Utilizando o matplotlib como backend")
else:
    print("Utilizando o plotly como backend")

Utilizando o plotly como backend


In [2]:
import tensorflow as tf

from sklearn.model_selection import train_test_split
from tensorflow import keras

EarlyStopping = keras.callbacks.EarlyStopping
Sequential = keras.models.Sequential
Dense = keras.layers.Dense
Dropout = keras.layers.Dropout

In [3]:
mat = pd.DataFrame(loadmat('dadosIAdisciplina.mat'))
mat

H1     L      N1      N2    PH1    PH2       Q1       Q2 SP_PH1  \
0     [45.2]  8641   [9.8]  [13.4]  [6.9]  [7.0]  [480.3]  [471.5]  [6.9]   
1     [45.4]  8641   [9.8]  [13.3]  [6.9]  [7.0]  [479.7]  [470.7]  [6.9]   
2     [45.2]  8641   [9.8]  [13.2]  [6.9]  [7.0]  [479.5]  [470.5]  [6.9]   
3     [44.9]  8641   [9.7]  [13.1]  [6.9]  [7.1]  [480.8]  [470.9]  [6.9]   
4     [45.1]  8641   [9.7]  [13.0]  [6.9]  [7.1]  [480.1]  [471.4]  [6.9]   
...      ...   ...     ...     ...    ...    ...      ...      ...    ...   
8636  [46.2]  8641  [15.0]  [21.3]  [7.0]  [7.0]  [485.2]  [481.0]  [6.9]   
8637  [46.3]  8641  [15.0]  [21.3]  [7.0]  [7.0]  [485.2]  [480.3]  [6.9]   
8638  [46.7]  8641  [15.0]  [21.3]  [7.0]  [7.0]  [484.9]  [480.1]  [6.9]   
8639  [46.7]  8641  [15.0]  [21.4]  [7.0]  [7.0]  [484.8]  [480.2]  [6.9]   
8640  [46.9]  8641  [15.0]  [21.4]  [7.0]  [7.0]  [485.3]  [480.8]  [6.9]   

     SP_PH2  SP_Q1        t  
0       [7]  [480]      [1]  
1       [7]  [480]     [11]  
2       [7]  [480]     [21]  
3       [7]  [480]     [31]  
4       [7]  [480]     [41]  
...     ...    ...      ...  
8636    [7]  [485]  [86361]  
8637    [7]  [485]  [86371]  
8638    [7]  [485]  [86381]  
8639    [7]  [485]  [86391]  
8640    [7]  [485]  [86401]  

[8641 rows x 12 columns]

In [4]:
df = pd.DataFrame()

df['N1'] = mat['N1'].apply(lambda x:x[0])
df['N2'] = mat['N2'].apply(lambda x:x[0])
df['Q1'] = mat['Q1'].apply(lambda x:x[0])
df['H1'] = mat['H1'].apply(lambda x:x[0])
df['Q2'] = mat['Q2'].apply(lambda x:x[0])

df.plot()

In [5]:
df2 = df.copy()

df2['Q1'].iloc[7670:7751] = np.NAN
df2.iloc[5330:5500] = np.NAN

# slinear, quadratic, cubic, spline, barycentric,
df2 = df2.interpolate(method='spline', order=3)

df2.plot()

In [6]:
df3 = df2.rolling(window=20).mean().dropna()
df3.plot()

In [7]:
scaler = MinMaxScaler().fit(df3)
dfn = pd.DataFrame(scaler.transform(df3), columns=['N1', 'N2', 'Q1', 'H1','Q2'])

x = dfn[['N1', 'N2', 'Q1', 'H1']]
y = dfn[['Q2']]

X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.25)

dfn.plot()

In [8]:
cb = EarlyStopping(monitor='val_loss', mode='min', patience=20)

model = Sequential()
model.add(Dense(20, activation='tanh', input_dim=4))
model.add(Dense(15, activation='tanh'))
model.add(Dense(5, activation='tanh'))
model.add(Dense(1, activation='sigmoid'))

model.compile(loss='msle', optimizer='adam', metrics=['mse'])
hist = model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=10000, batch_size=300, callbacks=[cb])

to_plot = pd.DataFrame()
to_plot['Q2'] = y['Q2']
to_plot['Q2_predicted'] = model.predict(x)
to_plot.plot()

 0.0040
Epoch 1391/10000
22/22 [==============================] - 0s 2ms/step - loss: 0.0018 - mse: 0.0042 - val_loss: 0.0018 - val_mse: 0.0040
Epoch 1392/10000
22/22 [==============================] - 0s 2ms/step - loss: 0.0018 - mse: 0.0042 - val_loss: 0.0018 - val_mse: 0.0041
Epoch 1393/10000
22/22 [==============================] - 0s 2ms/step - loss: 0.0018 - mse: 0.0042 - val_loss: 0.0018 - val_mse: 0.0040
Epoch 1394/10000
22/22 [==============================] - 0s 2ms/step - loss: 0.0018 - mse: 0.0042 - val_loss: 0.0018 - val_mse: 0.0040
Epoch 1395/10000
22/22 [==============================] - 0s 2ms/step - loss: 0.0018 - mse: 0.0042 - val_loss: 0.0018 - val_mse: 0.0042
Epoch 1396/10000
22/22 [==============================] - 0s 3ms/step - loss: 0.0019 - mse: 0.0043 - val_loss: 0.0018 - val_mse: 0.0042
Epoch 1397/10000
22/22 [==============================] - 0s 3ms/step - loss: 0.0018 - mse: 0.0042 - val_loss: 0.0018 - val_mse: 0.0040
Epoch 1398/10000
22/22 [================

In [10]:
raw_data_normalized = pd.DataFrame(scaler.transform(df), columns=['N1', 'N2', 'Q1', 'H1', 'Q2'])

raw_data_normalized = raw_data_normalized.rolling(10).mean().dropna()

to_input = raw_data_normalized[['N1', 'N2', 'Q1', 'H1']]

to_plot = pd.DataFrame()
to_plot['Q2'] = raw_data_normalized['Q2']
to_plot['Q2_predicted'] = model.predict(to_input)
to_plot.plot()